In [3]:
%load_ext autoreload
%autoreload 2

In [4]:
from datetime import datetime

import branca
import folium
import geojson
import geopandas as gpd
import pandas as pd
import pytz
import requests
from dateutil.relativedelta import relativedelta

In [5]:
current_hour = datetime.utcnow().replace(tzinfo=pytz.UTC, minute=0, second=0, microsecond=0)

month_ago_same_hour = current_hour - relativedelta(months=1)
month_ago_same_hour_s = month_ago_same_hour.strftime('%Y-%m-%dT%H:%M:%SZ')

last_month_same_hour_same_weekday = []
week_ago = current_hour - relativedelta(days=7)
while week_ago >= month_ago_same_hour:
    last_month_same_hour_same_weekday.append(week_ago)
    week_ago = week_ago - relativedelta(days=7)


In [6]:
crowd = requests.get(
    f'https://api.data.amsterdam.nl/v1/wfs/crowdmonitor/?SERVICE=WFS&VERSION=2.0.0&REQUEST=GetFeature&TYPENAMES=passanten&OUTPUTFORMAT=geojson&Filter=%3CFilter%3E%3CPropertyIsGreaterThan%3E%3CPropertyName%3Edatum_uur%3C/PropertyName%3E%3CLiteral%3E{month_ago_same_hour_s}%3C/Literal%3E%3C/PropertyIsGreaterThan%3E%3C/Filter%3E').content

crowd_geojson = geojson.loads(crowd)
crowd_geojson

{"crs": {"properties": {"name": "urn:ogc:def:crs:EPSG::28992"}, "type": "name"}, "features": [{"geometry": {"coordinates": [124564.763352, 480648.958691], "type": "Point"}, "geometry_name": "CTO Boulevard 2", "id": "passanten.5976", "properties": {"aantal_passanten": 0, "datum_uur": "2022-02-13T20:00:00+00:00", "gebied": "Arena", "id": 5976, "naam_locatie": "CTO Boulevard 2", "periode": "uur", "sensor": "CMSA-GAABM-02"}, "type": "Feature"}, {"geometry": {"coordinates": [124564.763352, 480648.958691], "type": "Point"}, "geometry_name": "CTO Boulevard 2", "id": "passanten.5977", "properties": {"aantal_passanten": 0, "datum_uur": "2022-02-13T21:00:00+00:00", "gebied": "Arena", "id": 5977, "naam_locatie": "CTO Boulevard 2", "periode": "uur", "sensor": "CMSA-GAABM-02"}, "type": "Feature"}, {"geometry": {"coordinates": [124564.763352, 480648.958691], "type": "Point"}, "geometry_name": "CTO Boulevard 2", "id": "passanten.5978", "properties": {"aantal_passanten": 0, "datum_uur": "2022-02-13T22

In [7]:
crowd_gdf = gpd.GeoDataFrame.from_features(crowd_geojson['features'])
crowd_gdf

geometry      id         sensor periode  \
0      POINT (124564.763 480648.959)    5976  CMSA-GAABM-02     uur   
1      POINT (124564.763 480648.959)    5977  CMSA-GAABM-02     uur   
2      POINT (124564.763 480648.959)    5978  CMSA-GAABM-02     uur   
3      POINT (124564.763 480648.959)    5979  CMSA-GAABM-02     uur   
4      POINT (124564.763 480648.959)    5980  CMSA-GAABM-02     uur   
...                              ...     ...            ...     ...   
22820                           None  411862        GVCV-07    week   
22821                           None  411912        GVCV-08    week   
22822                           None  411913        GVCV-08    week   
22823                           None  411914        GVCV-08    week   
22824                           None  411915        GVCV-08    week   

                        naam_locatie                  datum_uur  \
0                    CTO Boulevard 2  2022-02-13T20:00:00+00:00   
1                    CTO Boulevard 2  2022-02-13T21:00:00+00:00   
2                    CTO Boulevard 2  2022-02-13T22:00:00+00:00   
3                    CTO Boulevard 2  2022-02-13T23:00:00+00:00   
4                    CTO Boulevard 2  2022-02-14T00:00:00+00:00   
...                              ...                        ...   
22820       Pontsteiger N (ri. NDSM)  2022-03-06T23:00:00+00:00   
22821  Pontsteiger Z (ri. Distelweg)  2022-02-13T23:00:00+00:00   
22822  Pontsteiger Z (ri. Distelweg)  2022-02-20T23:00:00+00:00   
22823  Pontsteiger Z (ri. Distelweg)  2022-02-27T23:00:00+00:00   
22824  Pontsteiger Z (ri. Distelweg)  2022-03-06T23:00:00+00:00   

       aantal_passanten gebied  
0                     0  Arena  
1                     0  Arena  
2                     0  Arena  
3                     0  Arena  
4                     0  Arena  
...                 ...    ...  
22820              9023   None  
22821              3412   None  
22822              2968   None  
22823              4834   None  
22824              5009   None  

[22825 rows x 8 columns]

In [8]:
crowd_gdf.rename(columns={'periode': 'period', 'naam_locatie': 'location_name', 'datum_uur': 'datetime',
                          'aantal_passanten': 'people_count', 'gebied': 'area'}, inplace=True)
crowd_gdf

geometry      id         sensor period  \
0      POINT (124564.763 480648.959)    5976  CMSA-GAABM-02    uur   
1      POINT (124564.763 480648.959)    5977  CMSA-GAABM-02    uur   
2      POINT (124564.763 480648.959)    5978  CMSA-GAABM-02    uur   
3      POINT (124564.763 480648.959)    5979  CMSA-GAABM-02    uur   
4      POINT (124564.763 480648.959)    5980  CMSA-GAABM-02    uur   
...                              ...     ...            ...    ...   
22820                           None  411862        GVCV-07   week   
22821                           None  411912        GVCV-08   week   
22822                           None  411913        GVCV-08   week   
22823                           None  411914        GVCV-08   week   
22824                           None  411915        GVCV-08   week   

                       location_name                   datetime  people_count  \
0                    CTO Boulevard 2  2022-02-13T20:00:00+00:00             0   
1                    CTO Boulevard 2  2022-02-13T21:00:00+00:00             0   
2                    CTO Boulevard 2  2022-02-13T22:00:00+00:00             0   
3                    CTO Boulevard 2  2022-02-13T23:00:00+00:00             0   
4                    CTO Boulevard 2  2022-02-14T00:00:00+00:00             0   
...                              ...                        ...           ...   
22820       Pontsteiger N (ri. NDSM)  2022-03-06T23:00:00+00:00          9023   
22821  Pontsteiger Z (ri. Distelweg)  2022-02-13T23:00:00+00:00          3412   
22822  Pontsteiger Z (ri. Distelweg)  2022-02-20T23:00:00+00:00          2968   
22823  Pontsteiger Z (ri. Distelweg)  2022-02-27T23:00:00+00:00          4834   
22824  Pontsteiger Z (ri. Distelweg)  2022-03-06T23:00:00+00:00          5009   

        area  
0      Arena  
1      Arena  
2      Arena  
3      Arena  
4      Arena  
...      ...  
22820   None  
22821   None  
22822   None  
22823   None  
22824   None  

[22825 rows x 8 columns]

In [9]:
crowd_gdf['datetime'] = pd.to_datetime(crowd_gdf['datetime'])
crowd_gdf = crowd_gdf[crowd_gdf['period'] == 'uur'].drop(columns=['period'])
crowd_gdf

geometry      id         sensor  \
0      POINT (124564.763 480648.959)    5976  CMSA-GAABM-02   
1      POINT (124564.763 480648.959)    5977  CMSA-GAABM-02   
2      POINT (124564.763 480648.959)    5978  CMSA-GAABM-02   
3      POINT (124564.763 480648.959)    5979  CMSA-GAABM-02   
4      POINT (124564.763 480648.959)    5980  CMSA-GAABM-02   
...                              ...     ...            ...   
21727  POINT (120883.246 489471.311)  381577        GVCV-08   
21728  POINT (120883.246 489471.311)  381578        GVCV-08   
21729  POINT (120883.246 489471.311)  381579        GVCV-08   
21730  POINT (120883.246 489471.311)  381580        GVCV-08   
21731  POINT (120883.246 489471.311)  381581        GVCV-08   

                       location_name                  datetime  people_count  \
0                    CTO Boulevard 2 2022-02-13 20:00:00+00:00             0   
1                    CTO Boulevard 2 2022-02-13 21:00:00+00:00             0   
2                    CTO Boulevard 2 2022-02-13 22:00:00+00:00             0   
3                    CTO Boulevard 2 2022-02-13 23:00:00+00:00             0   
4                    CTO Boulevard 2 2022-02-14 00:00:00+00:00             0   
...                              ...                       ...           ...   
21727  Pontsteiger Z (ri. Distelweg) 2022-03-11 16:00:00+00:00            92   
21728  Pontsteiger Z (ri. Distelweg) 2022-03-11 17:00:00+00:00            25   
21729  Pontsteiger Z (ri. Distelweg) 2022-03-11 18:00:00+00:00             0   
21730  Pontsteiger Z (ri. Distelweg) 2022-03-11 19:00:00+00:00             0   
21731  Pontsteiger Z (ri. Distelweg) 2022-03-11 21:00:00+00:00             0   

           area  
0         Arena  
1         Arena  
2         Arena  
3         Arena  
4         Arena  
...         ...  
21727  IJ-veren  
21728  IJ-veren  
21729  IJ-veren  
21730  IJ-veren  
21731  IJ-veren  

[21732 rows x 7 columns]

In [10]:
crowd_last_month_same_hour_same_weekday_gdf = crowd_gdf[crowd_gdf['datetime'].isin(last_month_same_hour_same_weekday)]
mean_crowd_same_weekday_per_sensor_gdf = crowd_last_month_same_hour_same_weekday_gdf.groupby('sensor')[
    'people_count'].mean().apply(round)
mean_crowd_same_weekday_per_sensor_gdf

sensor
CMSA-GAABM-02       0
CMSA-GAABM-03       0
CMSA-GAABM-04      35
CMSA-GAABM-05      45
CMSA-GAKH-01       56
CMSA-GAWW-11     1355
CMSA-GAWW-12     1247
CMSA-GAWW-13      943
CMSA-GAWW-14      213
CMSA-GAWW-15     1336
CMSA-GAWW-16     1447
CMSA-GAWW-17      532
CMSA-GAWW-19      793
CMSA-GAWW-20     1053
CMSA-GAWW-21     1320
CMSA-GAWW-22      443
CMSA-GAWW-23      332
CMSA-GAWW-24      647
GABW-01-K           0
GABW-02-B           0
GABW-03-D           0
GABW-04-H           0
GABW-05-Oost        0
GABW-06-West        0
GACM-01           230
GACM-02           199
GACM-03           146
GACM-04           724
GADM-01-total      74
GADM-01-zone0      16
GVCV-01           143
GVCV-03           224
GVCV-04           275
GVCV-05            29
GVCV-06            26
GVCV-07            44
GVCV-08             0
Name: people_count, dtype: int64

In [11]:
def calculate_crowd_level(people_count_normalized):
    if people_count_normalized < .25:
        return 0
    elif people_count_normalized < .5:
        return 1
    elif people_count_normalized < .75:
        return 2
    else:
        return 3


current_crowd_prediction_gdf = crowd_last_month_same_hour_same_weekday_gdf.drop_duplicates(subset=['sensor']).drop(
    columns=['people_count', 'datetime'])
current_crowd_prediction_gdf = pd.merge(current_crowd_prediction_gdf, mean_crowd_same_weekday_per_sensor_gdf,
                                        on='sensor', how='left')

people_counts = current_crowd_prediction_gdf['people_count']
current_crowd_prediction_gdf['people_count_normalized'] = (people_counts - people_counts.min()) / (
        people_counts.max() - people_counts.min())
current_crowd_prediction_gdf['crowd_level'] = current_crowd_prediction_gdf['people_count_normalized'].apply(
    calculate_crowd_level)
current_crowd_prediction_gdf

geometry      id         sensor  \
0   POINT (124564.763 480648.959)    6143  CMSA-GAABM-02   
1   POINT (124724.351 480617.937)   12785  CMSA-GAABM-03   
2   POINT (124776.944 480609.159)   19408  CMSA-GAABM-04   
3   POINT (124908.114 480592.114)   26015  CMSA-GAABM-05   
4   POINT (121281.371 487310.488)   34127   CMSA-GAKH-01   
5   POINT (121811.237 487527.430)   42205   CMSA-GAWW-11   
6   POINT (121733.040 487443.837)   50304   CMSA-GAWW-12   
7   POINT (121663.807 487286.193)   59064   CMSA-GAWW-13   
8   POINT (121653.924 487355.579)   67824   CMSA-GAWW-14   
9   POINT (121699.440 487339.027)   76573   CMSA-GAWW-15   
10  POINT (121733.165 487351.261)   85333   CMSA-GAWW-16   
11  POINT (121593.241 487324.835)   94093   CMSA-GAWW-17   
12  POINT (121785.661 487420.451)  102853   CMSA-GAWW-19   
13  POINT (121651.762 487610.176)  111613   CMSA-GAWW-20   
14  POINT (121521.162 487230.523)  120227   CMSA-GAWW-21   
15  POINT (121750.346 487182.241)  128987   CMSA-GAWW-22   
16  POINT (121809.783 487321.371)  137717   CMSA-GAWW-23   
17  POINT (121775.218 487740.639)  146443   CMSA-GAWW-24   
18  POINT (121833.466 488119.339)  162996      GABW-01-K   
19  POINT (121853.015 488120.320)  171608      GABW-02-B   
20  POINT (121939.329 488065.664)  179918      GABW-03-D   
21  POINT (121913.740 488067.728)  188448      GABW-04-H   
22  POINT (121947.411 488052.369)  196837   GABW-05-Oost   
23  POINT (121878.875 488097.893)  205314   GABW-06-West   
24  POINT (121251.914 487076.025)  213781        GACM-01   
25  POINT (121339.868 487439.827)  222429        GACM-02   
26  POINT (121307.789 487080.205)  230920        GACM-03   
27  POINT (121693.937 487795.041)  239662        GACM-04   
28  POINT (121348.414 487364.886)  250494  GADM-01-total   
29  POINT (121348.414 487364.886)  259230  GADM-01-zone0   
30  POINT (121762.593 488201.698)  340434        GVCV-01   
31  POINT (121784.058 488188.980)  348523        GVCV-03   
32  POINT (121795.166 488183.253)  356663        GVCV-04   
33  POINT (122126.750 487988.750)  363824        GVCV-05   
34  POINT (124363.931 487898.780)  369571        GVCV-06   
35  POINT (120873.498 489484.030)  376295        GVCV-07   
36  POINT (120883.246 489471.311)  381396        GVCV-08   

                                location_name                  area  \
0                             CTO Boulevard 2                 Arena   
1                             CTO Boulevard 3                 Arena   
2                             CTO Boulevard 4                 Arena   
3                             CTO Boulevard 5                 Arena   
4                       Kalverstraat t.h.v. 1  Winkelgebied centrum   
5                                Korte Niezel                Wallen   
6                             Oudekennissteeg                Wallen   
7                                  Stoofsteeg                Wallen   
8             Oudezijds Voorburgwal t.h.v. 91                Wallen   
9           Oudezijds Achterburgwal t.h.v. 86                Wallen   
10          Oudezijds Achterburgwal t.h.v. 91                Wallen   
11           Oudezijds Voorburgwal t.h.v. 206                Wallen   
12                                 Molensteeg                Wallen   
13                              Oudebrugsteeg                Wallen   
14                                  Damstraat                Wallen   
15                          Kloveniersburgwal                Wallen   
16                                Bloedstraat                Wallen   
17                            Nieuwebrugsteeg                Wallen   
18                   Busplatform CS - Halte K        Busplatform CS   
19                   Busplatform CS - Halte B        Busplatform CS   
20                   Busplatform CS - Halte D        Busplatform CS   
21                   Busplatform CS - Halte H        Busplatform CS   
22    Busplatform CS - Oost (Trapopgang Oost)        Busplatform CS   
23  Busplatform CS - West (Trapopgang mi

In [13]:
from shapely.geometry import mapping, shape

# center = current_crowd_prediction_gdf.iloc[0]['geometry']          # Null Island
# circle = center.buffer(0.3)  # Degrees Radius
# print(geojson.dumps(mapping(circle)))

current_crowd_prediction_gdf['points_with_radius'] = current_crowd_prediction_gdf['geometry'].apply(lambda point: shape(point).buffer(20))
current_crowd_prediction_gdf.set_geometry('points_with_radius', inplace=True)

In [14]:
m = folium.Map(
    location=[52.3676, 4.9041],
    tiles="cartodbpositron",
    zoom_start=13
)

In [15]:
colorscale = branca.colormap.step.RdYlGn_04.scale(0, 3)

current_crowd_prediction_gdf.crs = 'urn:ogc:def:crs:EPSG::28992'
folium.GeoJson(current_crowd_prediction_gdf[['points_with_radius', 'crowd_level']], name="crowd",
               style_function=lambda feature: {'color': colorscale(feature['properties']['crowd_level'])}).add_to(m)
folium.LayerControl().add_to(m)
m